In [1]:
if 'dbutils' in locals():
    dbutils.library.restartPython()

!python --version

Python 3.11.9


In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [4]:
need_to_setup_env = False
need_to_setup_env

False

In [5]:
if need_to_setup_env:
    %pip config set global.index-url https://artifacts.forge.mastercard.com/artifactory/api/pypi/python/simple
    %pip install tf-keras
    %pip install -q --upgrade accelerate einops xformers torchvision
    %pip install -r requirements.txt
    !cd ../LLaMA-Factory && pip install -e .[torch,bitsandbytes] && FLASH_ATTENTION_FORCE_BUILD=TRUE pip install --upgrade flash-attn

In [6]:
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/logical-reasoning


In [7]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/logical-reasoning/.env


True

In [8]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

internlm/internlm2_5-7b-chat-1m None True datasets/mgtv results/results/mgtv-results_temp.csv


In [9]:
!nvidia-smi

Wed Jul 10 07:10:55 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   50C    P0              30W / 150W |      0MiB / 12282MiB |      6%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [10]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 4.61 ms, sys: 7.63 ms, total: 12.2 ms
Wall time: 636 ms


In [11]:
import os
import pandas as pd
from llm_toolkit.logical_reasoning_utils import *
from llm_toolkit.llm_utils import *

def load_data(alpaca_data_path="llama-factory/data/alpaca_mgtv_p1.json"):
    if os.path.exists(alpaca_data_path):
        print("loading existing data from:", alpaca_data_path)
        data = pd.read_json(alpaca_data_path, orient="records", lines=False)
        return data

    print("loading new data from:", alpaca_data_path)
    datasets = load_logical_reasoning_dataset(
        data_path, chinese_prompt=not use_english_datasets
    )
    df_train = datasets["train"].to_pandas()
    df_train["instruction"] = df_train.apply(
        lambda x: P1.format(x["puzzle"], x["truth"], x["text"]), axis=1
    )

    df_alpaca = pd.DataFrame(
        {"instruction": [""] * len(df_train), "input": [""] * len(df_train)}
    )
    df_alpaca["instruction"] = df_train["instruction"]
    df_alpaca["output"] = df_train["label"]
    df_alpaca.to_json(alpaca_data_path, orient="records", lines=False, indent=2)
    return df_alpaca

loading /home/inflaton/code/projects/courses/logical-reasoning/llm_toolkit/logical_reasoning_utils.py


In [12]:
df_alpaca = load_data()
print_row_details(df_alpaca)

loading existing data from: llama-factory/data/alpaca_mgtv_p1.json
--------------------------------------------------
instruction: 你是一个逻辑游戏的主持人。游戏规则如下：

1. 参与者会得到一个谜题。
2. 参与者可以通过提问来获取线索，尝试解开谜题。
3. 对于每个问题，主持人将根据实际情况回答以下五个选项之一：是、不是、不重要、回答正确、问法错误。
4. 回答中不能添加任何其它信息，也不能省略选项中的任何一个字。例如，不可以把“不是”省略成“不”。
5. 参与者需要根据回答来推理，并最终找出谜题的正确答案。

请严格按照这些规则回答参与者提出的问题。

谜题: 在甄家村里，有一个古老的传说：每年南瓜丰收的季节，南瓜田里总有一个最大的南瓜会不翼而飞，村民们对此现象困惑不解。请找出南瓜失踪背后的原因。

实际情况: 真相原来与一位年迈的农夫有关。这位农夫年轻时，曾与一位美丽的姑娘相恋。他们约定在南瓜丰收的季节结婚。然而，命运弄人，姑娘在婚礼前的一场意外中离世。悲伤的农夫为了纪念心爱的姑娘，每年都会将最大的南瓜偷走，放到姑娘的墓前，以此寄托自己的哀思。这一行为延续了多年，成为了乡村里一个神秘的传说。

参与者提出的问题: 偷的人信神吗

--------------------------------------------------
input: 
--------------------------------------------------
output: 不是


In [13]:
%%time

!./scripts/tune-lf.sh config/internlm2_5_7b_lora_sft_4bit.yaml

Current Directory:
/home/inflaton/code/projects/courses/logical-reasoning/llama-factory
config/internlm2_5_7b_lora_sft_4bit.yaml:
 {
  "model_name_or_path": "internlm/internlm2_5-7b-chat-1m",
  "stage": "sft",
  "do_train": true,
  "finetuning_type": "lora",
  "lora_target": "all",
  "quantization_bit": 4,
  "loraplus_lr_ratio": 16.0,
  "upcast_layernorm": true,
  "dataset": "alpaca_mgtv_p1",
  "template": "chatml",
  "cutoff_len": 1024,
  "max_samples": 5000,
  "overwrite_cache": true,
  "preprocessing_num_workers": 16,
  "output_dir": "saves/internlm2_5_7b/lora/sft",
  "logging_steps": 100,
  "save_steps": 562,
  "plot_loss": true,
  "overwrite_output_dir": true,
  "per_device_train_batch_size": 1,
  "gradient_accumulation_steps": 8,
  "learning_rate": 0.0001,
  "num_train_epochs": 6.0,
  "lr_scheduler_type": "cosine",
  "warmup_ratio": 0.1,
  "bf16": true,
  "ddp_timeout": 180000000,
  "val_size": 0.1,
  "per_device_eval_batch_size": 1,
  "eval_strategy": "steps",
  "eval_steps": 56